In [1]:
from pymongo import MongoClient
import pprint
import pandas as pd
import numpy as np
from collections import defaultdict 
from elasticsearch import Elasticsearch
from elasticsearch.helpers import scan
from datetime import datetime
import json
import hashlib
from datetime import datetime, date

In [2]:
CONNECTION_STRING = "mongodb://localhost:27017"
client = MongoClient(CONNECTION_STRING)
db = client['accounts_services']
collection = db['daily_signup_stats_accounts']

In [11]:
def fetch_mongo_yearly(db):
    total_data = {}
    total_data = defaultdict(lambda: defaultdict(int))
    today = date.today()
    start_date = datetime(2015, 10, 3)
    end_date = datetime(today.year, today.month, today.day)
    
    mongo_json = db['daily_signup_stats_accounts']
    
    for item in mongo_json.find():
        
        stats = item['stats']
        reported_date = datetime.strptime(stats["report_date"], '%Y-%m-%dT%H:%M:%S.%fZ')
        
        if start_date <= reported_date <= end_date:
            year_key = reported_date.year
            month_key = (reported_date.year, reported_date.month)
            total_data[year_key]['yearly_count'] += sum(entry["count"] for entry in stats["account_type"])
            total_data[year_key]['cum_count'] += sum(entry["count"] for entry in stats["account_type"])
            for entry in stats["account_type"]:
                total_data[year_key][entry["_id"] + "_account_type"] += entry["count"]
            for entry in stats["user_from"]:
                user_key = entry["_id"] if entry["_id"] is not None else "null_user_from"
                total_data[year_key][user_key + "_user_from"] += entry["count"]
    return total_data

In [12]:
def data_to_elastic(total_data):
    es = Elasticsearch("http://localhost:9200")

    for year_key, year_data in total_data.items():
        doc_id = f"{year_key}"
        document = {
            "year": year_key,
            "yearly_count": year_data['yearly_count'],
            "cumulative_count": year_data['cum_count']
        }
        for key, value in year_data.items():
            if key not in ['yearly_count', 'cum_count']:
                document[key] = value
        resp = es.index(index=f"yearly_signup_stats_accounts_{year_key}", id=doc_id, body=document)
        print(f"yearly_signup_stats_accounts_{year_key} DONE")

In [14]:
total_data = fetch_mongo_yearly(db)
data_to_elastic(total_data)

yearly_signup_stats_accounts_2023 DONE
yearly_signup_stats_accounts_2015 DONE


C:\Users\admin\AppData\Local\Temp\ipykernel_6904\1881610962.py:14: ElasticsearchWarning: Elasticsearch built-in security features are not enabled. Without authentication, your cluster could be accessible to anyone. See https://www.elastic.co/guide/en/elasticsearch/reference/7.17/security-minimal-setup.html to enable security.
  resp = es.index(index=f"yearly_signup_stats_accounts_{year_key}", id=doc_id, body=document)
